In [1]:
import os
import random
import pandas as pd
import numpy as np
import csv
#import tensorflow as tf
import torch
from sklearn.model_selection import train_test_split
# !pip install datasets
#from google.colab import drive
import textwrap
import progressbar
import keras
!pip install sentencepiece
import sentencepiece
#from keras.preprocessing.sequence import pad_sequences
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
!pip install transformers
from transformers import BertForSequenceClassification, AdamW, BertConfig
from transformers import get_linear_schedule_with_warmup
import time
import datetime
import json

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 30.0 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 60.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 116.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.1/200.1 kB 29.2 MB/s eta 0:00:00


In [2]:
from google.colab import drive
drive.mount('/content/drive')
# folder_path="C:\\Users\\awast\\Desktop\\NLP\\Data\\Data"

Mounted at /content/drive


In [ ]:
# df = pd.read_csv("C:\\Users\\awast\\Desktop\\NLP\\Data\\Data\\ILDC_single\\ILDC_single\\ILDC_single.csv\\ILDC_single.csv")
# train_set = df.query(" split=='train' ")
# test_set = df.query(" split=='test' ")
# validation_set = df.query(" split=='dev' ")

# train_set = []
# with open('/content/drive/MyDrive/swiss_judgment/train_mt.jsonl') as f:
#     for line in f:
#         train_set.append(json.loads(line))

In [ ]:
# from datasets import load_dataset

# dataset = load_dataset('swiss_judgment_prediction', 'mt_en')

NameError: ignored

In [ ]:
dataset

DatasetDict({
    train: Dataset({
        features: ['id', 'year', 'text', 'label', 'language', 'region', 'canton', 'legal area', 'source_language'],
        num_rows: 59703
    })
    validation: Dataset({
        features: ['id', 'year', 'text', 'label', 'language', 'region', 'canton', 'legal area', 'source_language'],
        num_rows: 0
    })
    test: Dataset({
        features: ['id', 'year', 'text', 'label', 'language', 'region', 'canton', 'legal area', 'source_language'],
        num_rows: 0
    })
})

In [5]:
# train_set,validation_set=train_test_split(dataset['train'],test_size=0.02,shuffle=True)
# train_set=pd.DataFrame(train_set)
# # test_set=pd.DataFrame(dataset['test'])
# validation_set=pd.DataFrame(validation_set)
# torch.save(train_set,'/content/drive/MyDrive/swiss_judgment/train_set.pt')
# torch.save(validation_set,'/content/drive/MyDrive/swiss_judgment/validation_set.pt')
train_set=torch.load('/content/drive/MyDrive/swiss_judgment/train_set.pt')
validation_set=torch.load('/content/drive/MyDrive/swiss_judgment/validation_set.pt')

In [ ]:
pd.DataFrame(validation_set).head()

id  year                                               text  label  \
0  11872  2004  Facts: Facts: A. M._, geb. In 1977, it collaps...      0   
1   3152  2002  The facts are: A. The Prosecutor General of th...      0   
2   1238  2000  Divorce: A.-K.H._ and M.H._ married on 23. Sep...      0   
3   7792  2003  Facts: Facts: A. M._, born in 1949, was from 1...      0   
4  45966  2014  Facts: A. Against X._ was suspected of sexual ...      0   

  language                    region canton     legal area source_language  
0       en                    Zürich     zh  insurance law              de  
1       en          Région lémanique     ge     public law              fr  
2       en                       n/a    n/a      civil law              de  
3       en                    Zürich     zh  insurance law              de  
4       en  Northwestern Switzerland     ag      penal law              de

In [6]:
from transformers import PreTrainedModel, PreTrainedTokenizer, PretrainedConfig
from transformers import BertForSequenceClassification, BertTokenizer, BertConfig
from transformers import RobertaForSequenceClassification, RobertaTokenizer, RobertaConfig
from transformers import XLNetForSequenceClassification, XLNetTokenizer, XLNetConfig
from transformers import XLMForSequenceClassification, XLMTokenizer, XLMConfig
from transformers import DistilBertForSequenceClassification, DistilBertTokenizer, DistilBertConfig
tokenizer = DistilBertTokenizer.from_pretrained('distilbert-base-cased', do_lower_case=True)
MODEL_CLASSES = {
    'bert': (BertForSequenceClassification, BertTokenizer, BertConfig),
    'xlnet': (XLNetForSequenceClassification, XLNetTokenizer, XLNetConfig),
    'xlm': (XLMForSequenceClassification, XLMTokenizer, XLMConfig),
    'roberta': (RobertaForSequenceClassification, RobertaTokenizer, RobertaConfig),
    'distilbert': (DistilBertForSequenceClassification, DistilBertTokenizer, DistilBertConfig)}

model_type = 'distilbert' ###--> CHANGE WHAT MODEL YOU WANT HERE!!! <--###
model_class, tokenizer_class, config_class = MODEL_CLASSES[model_type]
model_name = 'distilbert-base-cased'

In [7]:
def att_masking(input_ids):
    attention_masks = []
    for sent in input_ids:
        att_mask = [int(token_id > 0) for token_id in sent]
        attention_masks.append(att_mask)
    return attention_masks

In [8]:
def grouped_input_ids(all_toks):
    splitted_toks = []
    l=0
    r=510
    while(l<len(all_toks)):
        splitted_toks.append(all_toks[l:min(r,len(all_toks))])
        l+=410
        r+=410

    CLS = tokenizer.cls_token
    SEP = tokenizer.sep_token
    e_sents = []
    for l_t in splitted_toks:
        l_t = l_t + [SEP] + [CLS]
        encoded_sent = tokenizer.convert_tokens_to_ids(l_t)
        e_sents.append(encoded_sent)

    e_sents = pad_sequences(e_sents, maxlen=512, value=0, dtype="long", padding="pre")
    att_masks = att_masking(e_sents)
    return e_sents, att_masks

In [9]:
def generate_np_files_for_training(dataf, tokenizer):
    all_input_ids, all_att_masks, all_labels = [], [], []
    for i in progressbar.progressbar(range(len(dataf['text']))):
        text = dataf['text'].iloc[i]
        toks = tokenizer.tokenize(text)
        if(len(toks) > 10000):
            toks = toks[len(toks)-10000:]

        splitted_input_ids, splitted_att_masks = grouped_input_ids(toks)
        doc_label = dataf['label'].iloc[i]
        print(len(splitted_input_ids))
        for j in range(len(splitted_input_ids)):
            all_input_ids.append(splitted_input_ids[j])
            all_att_masks.append(splitted_att_masks[j])
            all_labels.append(doc_label)

    return all_input_ids, all_att_masks, all_labels

In [10]:
from keras.utils import pad_sequences
#from keras.preprocessing.sequence import pad_sequences

In [11]:
from transformers import *

tokenizer = DistilBertTokenizer.from_pretrained('distilbert-base-uncased', do_lower_case=True)
# train_input_ids, train_att_masks, train_labels = generate_np_files_for_training(train_set, tokenizer)

/usr/local/lib/python3.9/dist-packages/transformers/generation_utils.py:24: FutureWarning: Importing `GenerationMixin` from `src/transformers/generation_utils.py` is deprecated and will be removed in Transformers v5. Import as `from transformers import GenerationMixin` instead.
  warnings.warn(
/usr/local/lib/python3.9/dist-packages/transformers/generation_tf_utils.py:24: FutureWarning: Importing `TFGenerationMixin` from `src/transformers/generation_tf_utils.py` is deprecated and will be removed in Transformers v5. Import as `from transformers import TFGenerationMixin` instead.
  warnings.warn(
/usr/local/lib/python3.9/dist-packages/transformers/generation_flax_utils.py:24: FutureWarning: Importing `FlaxGenerationMixin` from `src/transformers/generation_flax_utils.py` is deprecated and will be removed in Transformers v5. Import as `from transformers import FlaxGenerationMixin` instead.
  warnings.warn(


loading file vocab.txt from cache at /root/.cache/huggingface/hub/models--distilbert-base-uncased/snapshots/1c4513b2eedbda136f57676a34eea67aba266e5c/vocab.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--distilbert-base-uncased/snapshots/1c4513b2eedbda136f57676a34eea67aba266e5c/tokenizer_config.json


loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--distilbert-base-uncased/snapshots/1c4513b2eedbda136f57676a34eea67aba266e5c/config.json
Model config DistilBertConfig {
  "_name_or_path": "distilbert-base-uncased",
  "activation": "gelu",
  "architectures": [
    "DistilBertForMaskedLM"
  ],
  "attention_dropout": 0.1,
  "dim": 768,
  "dropout": 0.1,
  "hidden_dim": 3072,
  "initializer_range": 0.02,
  "max_position_embeddings": 512,
  "model_type": "distilbert",
  "n_heads": 12,
  "n_layers": 6,
  "pad_token_id": 0,
  "qa_dropout": 0.1,
  "seq_classif_dropout": 0.2,
  "sinusoidal_pos_embds": false,
  "tie_weights_": true,
  "transformers_version": "4.28.1",
  "vocab_size": 30522
}



In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

In [ ]:
# torch.save(train_input_ids,'/content/drive/MyDrive/swiss_judgment/train_input_ids.pt')
# torch.save(train_att_masks,'/content/drive/MyDrive/swiss_judgment/train_att_masks.pt')
# torch.save(train_labels,'/content/drive/MyDrive/swiss_judgment/train_labels.pt')

In [14]:
train_input_ids=torch.load('/content/drive/MyDrive/swiss_judgment/train_input_ids.pt')
train_att_masks=torch.load('/content/drive/MyDrive/swiss_judgment/train_att_masks.pt')
train_labels=torch.load('/content/drive/MyDrive/swiss_judgment/train_labels.pt')

In [13]:
def input_id_maker(dataf, tokenizer):
    input_ids = []
    lengths = []

    for i in progressbar.progressbar(range(len(dataf['text']))):
        sen = dataf['text'].iloc[i]
        sen = tokenizer.tokenize(sen, add_prefix_space=True)
        CLS = tokenizer.cls_token
        SEP = tokenizer.sep_token
        if(len(sen) > 510):
            sen = sen[len(sen)-510:]

    sen = sen + [SEP] + [CLS]
    encoded_sent = tokenizer.convert_tokens_to_ids(sen)
    input_ids.append(encoded_sent)
    lengths.append(len(encoded_sent))

    input_ids = pad_sequences(input_ids, maxlen=512, value=0, dtype="long", truncating="pre", padding="pre")
    return input_ids, lengths

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
validation_set.head()

NameError: ignored

In [ ]:
# validation_input_ids, validation_attention_masks, validation_labels = generate_np_files_for_training(validation_set, tokenizer)

  0% (4 of 1195) |                       | Elapsed Time: 0:00:00 ETA:   0:00:39

2
2
1
3
1
2
3


  0% (8 of 1195) |                       | Elapsed Time: 0:00:00 ETA:   0:00:39

3
2
2


  1% (16 of 1195) |                      | Elapsed Time: 0:00:00 ETA:   0:00:46

...

2
2
2
2
3
2
2
2
4
2
2
2
2
4
1


 98% (1176 of 1195) |################### | Elapsed Time: 0:00:27 ETA:   0:00:00

2
4
4
1
2
3
1
1
2
2
3
1
3
2


100% (1195 of 1195) |####################| Elapsed Time: 0:00:27 Time:  0:00:27


2
14
1
3
3
1
1
1
3
2
1


In [15]:
# torch.save(validation_input_ids,'/content/drive/MyDrive/swiss_judgment/validation_input_ids.pt')
# torch.save(validation_attention_masks,'/content/drive/MyDrive/swiss_judgment/validation_attention_masks.pt')
# torch.save(validation_labels,'/content/drive/MyDrive/swiss_judgment/validation_labels.pt')
validation_input_ids=torch.load('/content/drive/MyDrive/swiss_judgment/validation_input_ids.pt')
validation_attention_masks=torch.load('/content/drive/MyDrive/swiss_judgment/validation_attention_masks.pt')
validation_labels=torch.load('/content/drive/MyDrive/swiss_judgment/validation_labels.pt')
# validation_attention_masks = att_masking(validation_input_ids)
# validation_labels = validation_set['label'].to_numpy().astype('int')

In [ ]:
list(train_input_ids)

[(tensor([ 5860,    20,   648,    60,    24,     9,    18,    17,    23,     9,
           2732,    19,  1094,    25,  5243,    19,    27,  3837,  1007,    38,
             18,    17,   267,  3801,   167,   369,  3801,   454,  1007,    17,
             10, 20509,   153,  6783,    17,   267,  3801,    11,     9,    85,
             30,    31,  1334,     9,   116,   189,  8405,  1778,    37,    17,
           7841,     9,    17,  3983,     9,    37,    17,  7841,     9,    17,
           3983,     9,    18,    17,  6507,     9,  2709,    73,   237,  8308,
           4232,     9,    31,   198,     9,    25,    17,  6826, 23130,  1760,
             85,  4460,    22,    18,    17,   267,  3801,    24,  9837,  1696,
            535,  5373,   167,  8844,  4757,    20,  1875,     9,   116,   189,
           8405,  1778,    33,    18,  9429,    20,    17, 14780, 29316,   368,
          10296,    21,    17, 19616,    23,    25,  1425,  8308,  4232,    19,
             87,  4709,    20,    17,  7

In [16]:
train_inputs = train_input_ids
validation_inputs = validation_input_ids
train_masks = train_att_masks
validation_masks = validation_attention_masks

train_inputs = torch.tensor(train_inputs)
train_labels = torch.tensor(train_labels)
train_masks = torch.tensor(train_masks)
validation_inputs = torch.tensor(validation_inputs)
validation_labels = torch.tensor(validation_labels)
validation_masks = torch.tensor(validation_masks)

<ipython-input-16-2f7d7bad15bf>:6: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:245.)
  train_inputs = torch.tensor(train_inputs)


TypeError: ignored

In [ ]:
print(train_inputs.shape)
print(train_masks.shape)
print(train_labels.shape)

In [ ]:
print(validation_inputs.shape)
print(validation_masks.shape)
print(validation_labels.shape)

In [17]:
batch_size = 12
train_data = TensorDataset(train_inputs, train_masks, train_labels)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size = batch_size)
validation_data = TensorDataset(validation_inputs, validation_masks, validation_labels)
validation_sampler = RandomSampler(validation_data)
validation_dataloader = DataLoader(validation_data, sampler=validation_sampler, batch_size = batch_size)


In [19]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = DistilBertForSequenceClassification.from_pretrained("distilbert-base-cased", num_labels=2)
model.to(device)

loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--distilbert-base-cased/snapshots/4dc145c5bd4fdb672dcded7fdc1efd6c2bc55992/config.json
Model config DistilBertConfig {
  "activation": "gelu",
  "attention_dropout": 0.1,
  "dim": 768,
  "dropout": 0.1,
  "hidden_dim": 3072,
  "initializer_range": 0.02,
  "max_position_embeddings": 512,
  "model_type": "distilbert",
  "n_heads": 12,
  "n_layers": 6,
  "output_past": true,
  "pad_token_id": 0,
  "qa_dropout": 0.1,
  "seq_classif_dropout": 0.2,
  "sinusoidal_pos_embds": false,
  "tie_weights_": true,
  "transformers_version": "4.28.1",
  "vocab_size": 28996
}



loading weights file pytorch_model.bin from cache at /root/.cache/huggingface/hub/models--distilbert-base-cased/snapshots/4dc145c5bd4fdb672dcded7fdc1efd6c2bc55992/pytorch_model.bin
Some weights of the model checkpoint at distilbert-base-cased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.bias', 'vocab_layer_norm.bias', 'vocab_projector.bias', 'vocab_transform.weight', 'vocab_layer_norm.weight', 'vocab_projector.weight']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForS

DistilBertForSequenceClassification(
  (distilbert): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(28996, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0-5): 6 x TransformerBlock(
          (attention): MultiHeadSelfAttention(
            (dropout): Dropout(p=0.1, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.1, inplace=False)
 

In [20]:
lr = 2e-6
max_grad_norm = 1.0
epochs = 5
num_total_steps = len(train_dataloader)*epochs
num_warmup_steps = 1000
warmup_proportion = float(num_warmup_steps) / float(num_total_steps)  # 0.1
optimizer = AdamW(model.parameters(), lr=lr, correct_bias=True)
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps = num_warmup_steps, num_training_steps = num_total_steps)

def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()
    return np.sum(pred_flat == labels_flat) / len(labels_flat)

seed_val = 21


np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)

/usr/local/lib/python3.9/dist-packages/transformers/optimization.py:391: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [ ]:
train_loss_values = []
train_accuracy = []
val_loss_values = []
val_accuracy = []
PATH = "/content/drive/MyDrive/swiss_judgment/model.pt"
epochs=4


# For each epoch...
for epoch_i in range(0, epochs):
    print('======== Epoch {:} / {:} ========'.format(epoch_i + 1, epochs))
    print('Training...')
    
    model.train()
    total_loss=0
    train_batch_accuracy = 0

    for step, batch in enumerate(train_dataloader):
        if step % 40 == 0 and not step == 0:
            print('  Batch {:>5,}  of  {:>5,}. : loss: {:} '.format(step, len(train_dataloader), total_loss/step))


        b_input_ids = batch[0].to(device)
        b_input_mask = batch[1].to(device)
        b_labels = batch[2].to(device)

        model.zero_grad()        

        outputs = model(b_input_ids,labels=b_labels)
        loss, logits = outputs[:2]

        total_loss+=loss.item()

        loss.backward()

        batch_logits = logits
        logits = batch_logits.detach().cpu().numpy()
        label_ids = b_labels.to('cpu').numpy()
        train_batch_accuracy = flat_accuracy(logits, label_ids)

        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)

        optimizer.step()
        scheduler.step()

        if step%1000 == 0 and not step == 0:
            print("\nRunning Validation...")
            model.save_pretrained('/content/drive/MyDrive/swiss_judgment/model2')
            eval_loss, eval_accuracy = 0, 0
            nb_eval_steps, nb_eval_examples = 0, 0
            for batch in validation_dataloader:
                batch = tuple(t.to(device) for t in batch)
                b_input_ids, b_input_mask, b_labels = batch
                with torch.no_grad():        
                    outputs = model(b_input_ids, labels=b_labels)

                loss, logits = outputs[:2]
    
                logits = logits.detach().cpu().numpy()
                label_ids = b_labels.to('cpu').numpy()
        
                tmp_eval_accuracy = flat_accuracy(logits, label_ids)
                eval_accuracy += tmp_eval_accuracy

                eval_loss+=loss
 
                nb_eval_steps += 1

            val_accuracy.append(eval_accuracy/nb_eval_steps)
            val_loss_values.append(eval_loss/nb_eval_steps)

            print('Validation loss: {:} : Validation accuracy: {:}'.format(val_loss_values[-1], val_accuracy[-1]))

        
    model.save_pretrained('/content/drive/MyDrive/swiss_judgment/model2_epoch')
    train_loss_values.append(total_loss/len(train_dataloader))
    train_accuracy.append(train_batch_accuracy/len(train_dataloader))


print("Training complete!")

======== Epoch 1 / 4 ========
Training...
  Batch    40  of  11,328. : loss: 0.7297097951173782 
  Batch    80  of  11,328. : loss: 0.722038521617651 
  Batch   120  of  11,328. : loss: 0.7147034168243408 
  Batch   160  of  11,328. : loss: 0.705889892578125 
  Batch   200  of  11,328. : loss: 0.6932177034020424 
  Batch   240  of  11,328. : loss: 0.680017386501034 
  Batch   280  of  11,328. : loss: 0.6669717523668494 
  Batch   320  of  11,328. : loss: 0.653364188130945 
  Batch   360  of  11,328. : loss: 0.6448918009797732 
  Batch   400  of  11,328. : loss: 0.6355215564370156 
  Batch   440  of  11,328. : loss: 0.6236852077597922 
  Batch   480  of  11,328. : loss: 0.6159986241099735 
  Batch   520  of  11,328. : loss: 0.616618702130822 
  Batch   560  of  11,328. : loss: 0.6121000203437039 
  Batch   600  of  11,328. : loss: 0.6048095750560363 
  Batch   640  of  11,328. : loss: 0.6024951706407592 
  Batch   680  of  11,328. : loss: 0.6006683408994885 
  Batch   720  of  11,328. :

Configuration saved in /content/drive/MyDrive/swiss_judgment/model2/config.json



Running Validation...


Model weights saved in /content/drive/MyDrive/swiss_judgment/model2/pytorch_model.bin


Validation loss: 0.552570641040802 : Validation accuracy: 0.7607758620689654
  Batch 1,040  of  11,328. : loss: 0.580940268203043 
  Batch 1,080  of  11,328. : loss: 0.58058756083526 
  Batch 1,120  of  11,328. : loss: 0.5795062369134809 
  Batch 1,160  of  11,328. : loss: 0.5777680698782206 
  Batch 1,200  of  11,328. : loss: 0.5761669674515724 
  Batch 1,240  of  11,328. : loss: 0.5761970750146335 
  Batch 1,280  of  11,328. : loss: 0.5744037429918535 
  Batch 1,320  of  11,328. : loss: 0.5730626990736434 
  Batch 1,360  of  11,328. : loss: 0.5713656185961822 
  Batch 1,400  of  11,328. : loss: 0.5686703687906265 
  Batch 1,440  of  11,328. : loss: 0.5678785889409482 
  Batch 1,480  of  11,328. : loss: 0.568029949381142 
  Batch 1,520  of  11,328. : loss: 0.5671544227455008 
  Batch 1,560  of  11,328. : loss: 0.5671558861071483 
  Batch 1,600  of  11,328. : loss: 0.5672422812785953 
  Batch 1,640  of  11,328. : loss: 0.5673464561653573 
  Batch 1,680  of  11,328. : loss: 0.5670195276

...

Validation loss: 0.5077686905860901 : Validation accuracy: 0.7607758620689656
  Batch 3,040  of  11,328. : loss: 0.5100736487656832 
  Batch 3,080  of  11,328. : loss: 0.5104990880694482 
  Batch 3,120  of  11,328. : loss: 0.510315413835148 
  Batch 3,160  of  11,328. : loss: 0.5104536613614499 
  Batch 3,200  of  11,328. : loss: 0.5100571074942127 
  Batch 3,240  of  11,328. : loss: 0.5104620547712218 
  Batch 3,280  of  11,328. : loss: 0.5111879621836833 
  Batch 3,320  of  11,328. : loss: 0.511352883925639 
  Batch 3,360  of  11,328. : loss: 0.511193824798933 
  Batch 3,400  of  11,328. : loss: 0.5109511360175469 
  Batch 3,440  of  11,328. : loss: 0.51049678985376 
  Batch 3,480  of  11,328. : loss: 0.5103604086813913 
  Batch 3,520  of  11,328. : loss: 0.5100792986891147 
  Batch 3,560  of  11,328. : loss: 0.5104942439437917 
  Batch 3,600  of  11,328. : loss: 0.5101422925707366 
  Batch 3,640  of  11,328. : loss: 0.5102015128625291 
  Batch 3,680  of  11,328. : loss: 0.5103601158

Configuration saved in /content/drive/MyDrive/swiss_judgment/model2/config.json



Running Validation...


Model weights saved in /content/drive/MyDrive/swiss_judgment/model2/pytorch_model.bin


Validation loss: 0.5101609230041504 : Validation accuracy: 0.7622126436781611
  Batch 4,040  of  11,328. : loss: 0.5106608467416303 
  Batch 4,080  of  11,328. : loss: 0.5106954534738963 
  Batch 4,120  of  11,328. : loss: 0.5107875296900284 
  Batch 4,160  of  11,328. : loss: 0.5109309502125073 
  Batch 4,200  of  11,328. : loss: 0.5107957262652261 
  Batch 4,240  of  11,328. : loss: 0.5107768517620158 
  Batch 4,280  of  11,328. : loss: 0.5107585207498241 
  Batch 4,320  of  11,328. : loss: 0.5103908040008888 
  Batch 4,360  of  11,328. : loss: 0.509780189517988 
  Batch 4,400  of  11,328. : loss: 0.51000709683719 
  Batch 4,440  of  11,328. : loss: 0.5099116345448 
  Batch 4,480  of  11,328. : loss: 0.5100454062888665 
  Batch 4,520  of  11,328. : loss: 0.5099100409256937 
  Batch 4,560  of  11,328. : loss: 0.5102079590749845 
  Batch 4,600  of  11,328. : loss: 0.5103770906089441 
  Batch 4,640  of  11,328. : loss: 0.5103668525172719 
  Batch 4,680  of  11,328. : loss: 0.51040018633

In [ ]:
output_dir = '/content/drive/MyDrive/swiss_judgment/' # path to which fine tuned model is to be saved

# Create output directory if needed
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

print("Saving model to %s" % output_dir)

# Save a trained model, configuration and tokenizer using `save_pretrained()`.
# They can then be reloaded using `from_pretrained()`
model_to_save = model.module if hasattr(model, 'module') else model  # Take care of distributed/parallel training
model_to_save.save_pretrained(output_dir)
tokenizer.save_pretrained(output_dir)

# Good practice: save your training arguments together with the trained model
# torch.save(args, os.path.join(output_dir, 'training_args.bin'))

# Copy the model files to a directory in your Google Drive.
# !cp -r ./mini_XLNet/ "/content/Drive/My Drive/mini_XLNet/"

Saving model to /content/drive/MyDrive/swiss_judgment/


Configuration saved in /content/drive/MyDrive/swiss_judgment/config.json
Model weights saved in /content/drive/MyDrive/swiss_judgment/pytorch_model.bin
tokenizer config file saved in /content/drive/MyDrive/swiss_judgment/tokenizer_config.json
Special tokens file saved in /content/drive/MyDrive/swiss_judgment/special_tokens_map.json


('/content/drive/MyDrive/swiss_judgment/tokenizer_config.json',
 '/content/drive/MyDrive/swiss_judgment/special_tokens_map.json',
 '/content/drive/MyDrive/swiss_judgment/vocab.txt',
 '/content/drive/MyDrive/swiss_judgment/added_tokens.json')

In [ ]:

df = pd.read_csv('/content/Drive/My Drive/LNLP/dataset.csv')
train_set = df.query(" split=='train' ")
test_set = df.query(" split=='test' ")
validation_set = df.query(" split=='dev' ")

In [ ]:
output_dir = "/content/Drive/My Drive/mini_XLNet/"
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = XLNetForSequenceClassification.from_pretrained(output_dir, output_hidden_states=True)
tokenizer = tokenizer_class.from_pretrained(output_dir)
model.to(device)

In [ ]:
def att_masking(input_ids):
    attention_masks = []
    for sent in input_ids:
        att_mask = [int(token_id > 0) for token_id in sent]
        attention_masks.append(att_mask)
    return attention_masks

In [ ]:
def grouped_input_ids(all_toks):
    splitted_toks = []
    l=0
    r=510
    while(l<len(all_toks)):
        splitted_toks.append(all_toks[l:min(r,len(all_toks))])
        l+=410
        r+=410

    CLS = tokenizer.cls_token
    SEP = tokenizer.sep_token
    e_sents = []
    for l_t in splitted_toks:
        l_t = l_t + [SEP] + [CLS]
        encoded_sent = tokenizer.convert_tokens_to_ids(l_t)
        e_sents.append(encoded_sent)

    e_sents = pad_sequences(e_sents, maxlen=512, value=0, dtype="long", padding="pre")
    att_masks = att_masking(e_sents)
    return e_sents, att_masks

In [ ]:
def get_output_for_one_vec(input_id, att_mask):
    input_ids = torch.tensor(input_id)
    att_masks = torch.tensor(att_mask)
    input_ids = input_ids.unsqueeze(0)
    att_masks = att_masks.unsqueeze(0)
    model.eval()
    input_ids = input_ids.to(device)
    att_masks = att_masks.to(device)
    with torch.no_grad():
        logits, encoded_layers = model(input_ids=input_ids, token_type_ids=None, attention_mask=att_masks)

    vec = encoded_layers[12][0][-1]
    vec = vec.detach().cpu().numpy()
    return vec

In [ ]:
def generate_np_files_for_emb(dataf, tokenizer):
    all_docs = []
    for i in progressbar.progressbar(range(len(dataf['text']))):
        text = dataf['text'].iloc[i]
        toks = tokenizer.tokenize(text, add_prefix_space=True)
        if(len(toks) > 10000):
            toks = toks[len(toks)-10000:]

    splitted_input_ids, splitted_att_masks = grouped_input_ids(toks)

    vecs = []
    for index,ii in enumerate(splitted_input_ids):
        vecs.append(get_output_for_one_vec(ii, splitted_att_masks[index]))
 
    one_doc = np.asarray(vecs)
    all_docs.append(one_doc)

    all_docs = np.asarray(all_docs)
    return all_docs

In [ ]:
vecs_dev = generate_np_files_for_emb(validation_set, tokenizer)
np.save("/content/Drive/My Drive/LNLP/Hierarchical/XLNet_full/XLNet_dev.npy", vecs_dev)

In [ ]:
vecs_train = generate_np_files_for_emb(train_set, tokenizer)
np.save("/content/Drive/My Drive/LNLP/Hierarchical/XLNet_full/XLNet_train.npy", vecs_train)

In [ ]:
vecs_test = generate_np_files_for_emb(test_set, tokenizer)
np.save("/content/Drive/My Drive/LNLP/Hierarchical/XLNet_full/XLNet_test.npy", vecs_test)